In [92]:
import xml.etree.ElementTree as ET
from transformers import BertTokenizer, BertConfig
from transformers import BertModel
import nltk
import pandas as pd
import numpy as np
import re
import nltk
from sklearn import model_selection 
from sklearn.linear_model import LogisticRegression
import pickle
import string
from transformers import BertTokenizer, BertConfig
from transformers import BertModel
import torch
from nltk.corpus import stopwords
import os

In [44]:
tree = ET.parse('C:/Users/itsma/Documents/Capstone project/2012-07-15.original-annotation.release/1.xml')
root = tree.getroot()

text_section = root.find('TEXT')
text = text_section.text

tag_section = root.find('TAGS')
event_list = []
timex_list = []
tlink_list = []
sectime_list = []
for child in tag_section:
    if(child.tag=='EVENT'):
        event_list.append(child.attrib)
    elif(child.tag=='TIMEX3'):
        timex_list.append(child.attrib)
    elif(child.tag=='TLINK'):
        tlink_list.append(child.attrib)
    elif(child.tag=='SECTIME'):
        sectime_list.append(child.attrib)

for sub in event_list:
    sub["start"] = int(sub["start"])
    sub["end"] = int(sub["end"])

for sub in timex_list:
    sub["start"] = int(sub["start"])
    sub["end"] = int(sub["end"])

for sub in sectime_list:
    sub["start"] = int(sub["start"])
    sub["end"] = int(sub["end"])
    
    
event_list = sorted(event_list, key = lambda i: i['start'])
timex_list = sorted(timex_list, key = lambda i: i['start'])
sectime_list = sorted(sectime_list, key = lambda i: i['start'])


In [45]:
event_list

[{'id': 'E0',
  'start': 1,
  'end': 10,
  'text': 'Admission',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'OCCURRENCE'},
 {'id': 'E1',
  'start': 29,
  'end': 38,
  'text': 'Discharge',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'OCCURRENCE'},
 {'id': 'E2',
  'start': 128,
  'end': 140,
  'text': 'HIV positive',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'PROBLEM'},
 {'id': 'E3',
  'start': 161,
  'end': 170,
  'text': 'presented',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'EVIDENTIAL'},
 {'id': 'E4',
  'start': 176,
  'end': 200,
  'text': 'left upper quadrant pain',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'PROBLEM'},
 {'id': 'E5',
  'start': 212,
  'end': 218,
  'text': 'nausea',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'PROBLEM'},
 {'id': 'E6',
  'start': 223,
  'end': 231,
  'text': 'vomiting',
  'modality': 'FACTUAL',
  'polarity': 'POS',
  'type': 'PROBLEM'},
 {'id': 'E7',
  'start': 241,
  'end'

In [21]:
import nltk.data
bert_tokenizer = BertTokenizer.from_pretrained('C:/Users/itsma/Documents/BERT_models/NCBI_BERT_pubmed_mimic_uncased_L-12_H-768_A-12')
tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')

for entry in tokenizer.tokenize(text):
    print(bert_tokenizer.tokenize(entry))
    tokens = nltk.word_tokenize(entry)
    pos_tokens = nltk.pos_tag(tokens)
    for token in pos_tokens:
        print(token[0])
    break


['admission', 'date', ':', '09', '/', '29', '/', '1993', 'discharge', 'date', ':', '10', '/', '04', '/', '1993', 'history', 'of', 'present', 'illness', ':', 'the', 'patient', 'is', 'a', '28', '-', 'year', '-', 'old', 'woman', 'who', 'is', 'hiv', 'positive', 'for', 'two', 'years', '.']
Admission
Date
:
09/29/1993
Discharge
Date
:
10/04/1993
HISTORY
OF
PRESENT
ILLNESS
:
The
patient
is
a
28-year-old
woman
who
is
HIV
positive
for
two
years
.


In [22]:
def get_token_positions(input_text,token_list,start_from_pos=0):
    pos_list = []                    
    name_to_match = input_text.lower().replace(" ","")
    remaining_name = input_text.lower().replace(" ","")
    name = ""
    count = start_from_pos
    for entry in token_list[start_from_pos:]:
        if(remaining_name.startswith(entry.strip("##").lower())):
            pos_list.append(count)
            remaining_name = remaining_name[len(entry.strip("##").lower()):]
            name = name + entry.strip("##").lower()
            if(name == name_to_match):
                break
        else:
            pos_list = []
            name = ""
            remaining_name = name_to_match
            if(remaining_name.startswith(entry.strip("##").lower())):                                 
                pos_list.append(count)                                                                
                remaining_name = remaining_name[len(entry.strip("##").lower()):]
                name = name + entry.strip("##").lower()    
                if(name == name_to_match):                                   
                    break

        count = count + 1

    return pos_list

In [39]:
def process_string(string_input, padding_length):
    #string_input = re.sub(r"(\w)(["+ string.punctuation +"])", r"\1 \2 ", string_input)
    #string_input = string_input.replace("."," . ")

    tokenizer = nltk.data.load('tokenizers/punkt/english.pickle')
    sentences = tokenizer.tokenize(string_input)
    
    config = BertConfig.from_pretrained('C:/Users/itsma/Documents/BERT_models/NCBI_BERT_pubmed_mimic_uncased_L-12_H-768_A-12')
    config.output_hidden_states = True

    bert_tokenizer = BertTokenizer.from_pretrained('C:/Users/itsma/Documents/BERT_models/NCBI_BERT_pubmed_mimic_uncased_L-12_H-768_A-12')
    bert_model = BertModel.from_pretrained("C:/Users/itsma/Documents/BERT_models/NCBI_BERT_pubmed_mimic_uncased_L-12_H-768_A-12",config=config)
    #bert_tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
    #bert_model = BertModel.from_pretrained('bert-base-uncased')
    #stop_words = set(stopwords.words('english')) 
    
    positions_covered = 0
    word_list = []
    
    for index in range(len(sentences)):
        new_dict_sentence = {}
        sentence = sentences[index]
        new_dict_sentence["sentence"] = sentence
        new_dict_sentence["padding_length"] = padding_length
        start_index_bert = max(0,index-padding_length)
        end_index_bert = min(len(sentences),index+padding_length)

        bert_input = ' '.join(sentences[start_index_bert:(end_index_bert+1)])

        input_ids = torch.tensor(bert_tokenizer.encode(bert_input)).unsqueeze(0)  
        outputs = bert_model(input_ids)
        bert_vector = outputs[2][0][0].data.numpy()
        bert_tokens = bert_tokenizer.tokenize(bert_input)

        '''
        bert_vec_list = []
        for entry in range(0,len(outputs[0][0])):
            bert_vec_list.append(outputs[0][0][entry].data.numpy())

        bert_vector_sentence = np.mean(bert_vec_list,axis=0)
        '''
        start_pos = 0
        prior_pos = get_token_positions(' '.join(sentences[start_index_bert:index]),bert_tokens)
        
        if(len(prior_pos)>0):
            start_pos = max(prior_pos)
            
        tokens = nltk.word_tokenize(sentence)
        pos_tokens = nltk.pos_tag(tokens)

        sentence_covered = ''
        
        for token in pos_tokens:
            new_dict = {}
            current_word = token[0]
            new_dict["word"] = current_word
            token_position = string_input.find(current_word, positions_covered)
            spaces_between = string_input[positions_covered:token_position] 
            sentence_covered = sentence_covered + spaces_between + current_word
            positions_covered = token_position + len(current_word)
            new_dict["begin_pos"] = token_position
            new_dict["end_pos"] = positions_covered

            bert_token_positions = get_token_positions(current_word,bert_tokens,start_pos)
            vec_list = []
            if(len(bert_token_positions)==0):
                continue
            start_pos = bert_token_positions[-1] + 1

            for entry in bert_token_positions:
                vec_list.append(bert_vector[entry])
            
            bert_vector_word = np.mean(vec_list,axis=0)
            new_dict["keyword_vector"] = bert_vector_word

            word_list.append(new_dict)
    
    return word_list

In [84]:
processed_text = process_string(text,1)

In [88]:
processed_text

[{'word': 'Admission',
  'begin_pos': 1,
  'end_pos': 10,
  'keyword_vector': array([ 1.36540532e-01,  3.97017673e-02, -1.68897420e-01, -8.88842046e-02,
         -4.21210602e-02, -9.16283801e-02,  7.71307796e-02,  1.04038447e-01,
         -4.28351127e-02, -1.16676584e-01,  7.24766552e-02,  6.30533770e-02,
         -6.98354691e-02,  3.86799946e-02, -1.06367067e-01,  1.09939352e-01,
          6.50453344e-02,  4.02609259e-02,  7.83589333e-02, -6.31475076e-02,
         -5.65559603e-03, -5.87110370e-02, -6.78229779e-02, -4.29835264e-03,
         -5.19707203e-02, -1.84387304e-02, -1.30989224e-01,  5.53198159e-03,
         -1.26547545e-01,  6.72433525e-02, -4.08497751e-02, -3.11050788e-02,
         -4.32024300e-02,  5.07414490e-02, -9.13981907e-03, -1.34511888e-01,
         -3.69639210e-02,  5.41382656e-02,  1.26709446e-01,  5.47706634e-02,
         -9.35199112e-03, -8.11530203e-02, -5.37313819e-02, -5.38918003e-03,
         -7.09134936e-02,  2.00324897e-02, -2.47638726e+00, -6.12945184e-02,


In [87]:
def is_available_in_pos_list(dict_list, begin_pos, end_pos):
    for entry in dict_list:
        if(entry["start"]<=begin_pos and entry["end"]>=end_pos):
            return True
    
    return False


In [ ]:
def build_model_for_events():
    processed_text_df = pd.DataFrame(processed_text)
    
    pos_data = processed_text_df[processed_text_df["event_flag"]==1]
    neg_data = processed_text_df[processed_text_df["event_flag"]==0]
    
    pos_data_volume = len(pos_data)
    neg_data = neg_data.sample(4*pos_data_volume) #Maintaining a 1:9 ratio 

    combined_data = pd.concat([pos_data,neg_data])
    X = np.vstack(list(combined_data["keyword_vector"]))                                
    y = combined_data.chemical_label  
    X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=0.10, stratify=y, random_state=0)

    clf = LogisticRegression(random_state=0, solver='lbfgs',multi_class='ovr').fit(X_train, y_train)

    print("Score on test data:",clf.score(X_test,y_test))

    pickle.dump(clf,open(self.model_path,"wb"))
    return clf

In [89]:
class Discharge_note():
    def __init__(self, root):
        self.xml_root = root
        
    def process_note(self):
        root = self.xml_root
        text_section = root.find('TEXT')
        text = text_section.text
        
        self.processed_text = process_string(text,1)

        tag_section = root.find('TAGS')
        event_list = []
        timex_list = []
        tlink_list = []
        sectime_list = []
        for child in tag_section:
            if(child.tag=='EVENT'):
                event_list.append(child.attrib)
            elif(child.tag=='TIMEX3'):
                timex_list.append(child.attrib)
            elif(child.tag=='TLINK'):
                tlink_list.append(child.attrib)
            elif(child.tag=='SECTIME'):
                sectime_list.append(child.attrib)

        for sub in event_list:
            sub["start"] = int(sub["start"])
            sub["end"] = int(sub["end"])

        for sub in timex_list:
            sub["start"] = int(sub["start"])
            sub["end"] = int(sub["end"])

        for sub in sectime_list:
            sub["start"] = int(sub["start"])
            sub["end"] = int(sub["end"])


        event_list = sorted(event_list, key = lambda i: i['start'])
        timex_list = sorted(timex_list, key = lambda i: i['start'])
        sectime_list = sorted(sectime_list, key = lambda i: i['start'])
    
        for entry in self.processed_text:
            event_entry_available = is_available_in_pos_list(event_list,entry["begin_pos"],entry["end_pos"])
            timex_entry_available = is_available_in_pos_list(timex_list,entry["begin_pos"],entry["end_pos"])
            sectime_entry_available = is_available_in_pos_list(sectime_list,entry["begin_pos"],entry["end_pos"])

            entry.update({"event_flag":1 if event_entry_available else 0})
            entry.update({"timex_flag":1 if timex_entry_available else 0})
            entry.update({"sectime_flag":1 if sectime_entry_available else 0})
        

In [94]:
word_list = []
count = 0
for file in os.listdir("C:/Users/itsma/Documents/Capstone project/2012-07-15.original-annotation.release/"):
    if file.endswith(".xml"):
        try:
            file_name = os.path.join("C:/Users/itsma/Documents/Capstone project/2012-07-15.original-annotation.release/", file)
            tree = ET.parse(file_name)
            root = tree.getroot()
            discharge_note = Discharge_note(root)
            discharge_note.process_note()
            word_list.extend(discharge_note.processed_text)
            count = count + 1
            print(count)
            
        except:
            count = count + 1
            print("Error in processing file:",file)

1
2
3
4
5
6
7
8
9
Error in processing file: 143.xml
11
Error in processing file: 152.xml
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
Error in processing file: 23.xml
41
42
43
44
45
46
47
48
49
50
Error in processing file: 272.xml
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
Error in processing file: 382.xml
85
86
87
88
89
90
91
92
93
94
95
Error in processing file: 422.xml
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
Error in processing file: 547.xml
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
Error in processing file: 807.xml
184
185
186
187
188
189
190


In [95]:
len(word_list)

93034

In [96]:
word_list_df = pd.DataFrame(word_list)

In [124]:
pos_data = word_list_df[word_list_df["sectime_flag"]==1]
neg_data = word_list_df[word_list_df["sectime_flag"]==0]

In [119]:
pos_data_volume = len(pos_data)
neg_data = neg_data.sample(pos_data_volume)

In [126]:
len(pos_data)

326

In [129]:
combined_data = pd.concat([pos_data,neg_data])
X = np.vstack(list(combined_data["keyword_vector"]))                                
y = combined_data.sectime_flag  
X_train, X_test, y_train, y_test = model_selection.train_test_split(X, y, test_size=0.10, stratify=y, random_state=0)

clf = LogisticRegression(random_state=0, solver='lbfgs',multi_class='ovr').fit(X_train, y_train)

print("Score on test data:",clf.score(X_test,y_test))

C:\Users\itsma\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:947: ConvergenceWarning: lbfgs failed to converge. Increase the number of iterations.
  "of iterations.", ConvergenceWarning)


Score on test data: 0.9997850386930353


In [122]:
from sklearn import metrics

In [130]:
predictions = clf.predict(X_test)

cm = metrics.confusion_matrix(y_test, predictions)
print(cm)

[[9269    2]
 [   0   33]]
